In [1]:

# !pip install -q pyLDAvis
# !pip install contractions

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import csv
import nltk
import re
import pprint
import string
import contractions
import spacy
import en_core_web_sm
import gensim
import gensim.corpora as corpora
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis
import warnings
warnings.filterwarnings('ignore')

%matplotlib inline
from contractions import contractions_dict

from nltk import word_tokenize
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.stem.snowball import SnowballStemmer
from nltk.stem import WordNetLemmatizer

from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.manifold import TSNE
from sklearn import linear_model

from IPython.display import clear_output

from spacy import displacy

from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from pprint import pprint


[nltk_data] Downloading package punkt to /Users/shreyas/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/shreyas/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/shreyas/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
df = pd.read_csv('final_df.tsv', delimiter='\t', encoding="utf-8")
df = df.drop(['Unnamed: 0'], axis=1)

In [4]:
df

date  \
0     2022-09-16T14:00:00+00:00   
1     2022-09-16T13:49:38+00:00   
2     2022-09-16T13:35:41+00:00   
3     2022-09-16T13:34:07+00:00   
4     2022-09-16T12:53:41+00:00   
...                         ...   
1826  2022-08-05T21:20:00+00:00   
1827  2022-08-05T21:18:07+00:00   
1828  2022-08-05T21:02:17+00:00   
1829  2022-08-05T20:45:00+00:00   
1830  2022-08-05T20:22:45+00:00   

                                                  title  \
0                        Why Warren Buffett Loves Apple   
1     Big Tech stocks face difficulty beyond rising ...   
2     Dow Jones Sells Off As FedEx Plunges 23% On Pr...   
3     ARM listing: Why UK is desperate for Cambridge...   
4     Dow Jones Futures Sell Off As FedEx Plunges 20...   
...                                                 ...   
1826  Advertising Is Still Going Strong. Apple Wants...   
1827  Dow Jones Futures: Market Rally Resilient; App...   
1828  President Xi may use Speaker Pelosi's visit to...   
1829           The Best Multiport Wall Adapters of 2022   
1830  Amazon’s iRobot Deal Seen Facing Tough FTC Ant...   

                                                content    neg    pos  \
0     With a market capitalization of 25 trillion Ap...  0.000  0.129   
1     Yahoo Finance Live anchors discuss how inflati...  0.128  0.138   
2     The Dow Jones Industrial Average dived 350 poi...  0.102  0.217   
3     Arm which focuses on semiconductor and softwar...  0.040  0.048   
4     Dow Jones futures dropped 350 points Friday mo...  0.107  0.227   
...                                                 ...    ...    ...   
1826  A recent job listing suggests Apple is interes...  0.000  0.204   
1827  The market rally showed resilience after Frida...  0.000  0.000   
1828  Susan Shirk UC San Diego Research Professor an...  0.038  0.096   
1829  If you're tired of having all your gadgets spr...  0.165  0.094   
1830  Bloomberg  Amazoncom Inc is barrelling ahead w...  0.066  0.134   

      movement  subjectivity     polar  
0            0      0.166667  0.125000  
1            0      0.500000  0.136364  
2            0      0.450000  0.175000  
3            0      0.345402  0.086509  
4            0      0.500000  0.500000  
...        ...           ...       ...  
1826         1      0.283333  0.183333  
1827         1      0.000000  0.000000  
1828         1      0.401906  0.108931  
1829         1      0.400000 -0.216667  
1830         1      0.448494  0.099294  

[1831 rows x 8 columns]

In [5]:
corpus = [x for x in df['content']]

In [6]:
corpus

["With a market capitalization of 25 trillion Apple NASDAQ AAPL is one of the world's largest companies Since Buffett's lieutenants initially bought Berkshire's first 10 million shares in 2016 Buffett has come to appreciate Apple's business",
 'Yahoo Finance Live anchors discuss how inflation and fears of rising interest rates are affecting the tech sector',
 'The Dow Jones Industrial Average dived 350 points Friday as FedEx shares plunged more than 22 on a profit warning',
 'Arm which focuses on semiconductor and software design is owned by Japanese multinational conglomerate SoftBank Photo Neil HallReuters  British prime minister Liz Truss and chancellor Kwasi Kwarteng are preparing a lastditch effort to get Cambridge chipmaker Arm Holdings to list in London  The UK tech firm which focuses on semiconductor and software design is owned by Japanese multinational conglomerate SoftBank 9984T  The government is set to reignite highlevel talks with bosses at SoftBank once the official mour

Text Processing

In [7]:
tokens = [word_tokenize(corpu) for corpu in corpus]
text = nltk.Text(tokens)
text

<Text: ['With', 'a', 'market', 'capitalization', 'of', '25', 'trillion', 'Apple', 'NASDAQ', 'AAPL', 'is', 'one', 'of', 'the', 'world', "'s", 'largest', 'companies', 'Since', 'Buffett', "'s", 'lieutenants', 'initially', 'bought', 'Berkshire', "'s", 'first', '10', 'million', 'shares', 'in', '2016', 'Buffett', 'has', 'come', 'to', 'appreciate', 'Apple', "'s", 'business'] ['Yahoo', 'Finance', 'Live', 'anchors', 'discuss', 'how', 'inflation', 'and', 'fears', 'of', 'rising', 'interest', 'rates', 'are', 'affecting', 'the', 'tech', 'sector'] ['The', 'Dow', 'Jones', 'Industrial', 'Average', 'dived', '350', 'points', 'Friday', 'as', 'FedEx', 'shares', 'plunged', 'more', 'than', '22', 'on', 'a', 'profit', 'warning'] ['Arm', 'which', 'focuses', 'on', 'semiconductor', 'and', 'software', 'design', 'is', 'owned', 'by', 'Japanese', 'multinational', 'conglomerate', 'SoftBank', 'Photo', 'Neil', 'HallReuters', 'British', 'prime', 'minister', 'Liz', 'Truss', 'and', 'chancellor', 'Kwasi', 'Kwarteng', 'are'

In [8]:
stop_words = set(stopwords.words('english'))

stop_words.remove("not")
stop_words.add("The")
filtered_articles = [[word for word in article if not word in stop_words if word.isalpha()] for article in tokens]
print(stop_words)
print(filtered_articles)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [9]:
ps = PorterStemmer()

def nltk_stemmer(text):
  stemmed_articles = [[ps.stem(w) for w in filtered_article] for filtered_article in filtered_articles]
  return stemmed_articles

nltk_stemmed_articles = nltk_stemmer(filtered_articles)
print(nltk_stemmed_articles)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [10]:
wnl = WordNetLemmatizer()

def nltk_lemmatiser(text):
  lemmatised_articles = [[wnl.lemmatize(w) for w in filtered_article] for filtered_article in filtered_articles]
  return lemmatised_articles

nltk_lemmatised_articles = nltk_lemmatiser(filtered_articles)
print(nltk_lemmatised_articles)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [11]:
nlp = spacy.load('en_core_web_sm')

In [12]:
def spacy_lemmatiser(text):
  for filtered_article in filtered_articles:
    doc = nlp(' '.join(filtered_article))     
    for indexer, i in enumerate(doc):
      return filtered_articles

spacy_lemmatised_articles = spacy_lemmatiser(filtered_articles)
print(spacy_lemmatised_articles)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [13]:
CountVec = CountVectorizer(ngram_range=(1, 1), 
                           stop_words='english')
# Learn the vocabulary dictionary and transform to a vector of token counts
Count_data = CountVec.fit_transform(corpus) 
 
# Create dataframe that can be used for building models
cv_dataframe = pd.DataFrame(Count_data.toarray(),columns=CountVec.get_feature_names())
print(cv_dataframe)

      001  0015  002  0025  003  004  005  005930ks  006  007  ...  zooms  \
0       0     0    0     0    0    0    0         0    0    0  ...      0   
1       0     0    0     0    0    0    0         0    0    0  ...      0   
2       0     0    0     0    0    0    0         0    0    0  ...      0   
3       0     0    0     0    0    0    0         1    0    0  ...      0   
4       0     0    0     0    0    0    0         0    0    0  ...      0   
...   ...   ...  ...   ...  ...  ...  ...       ...  ...  ...  ...    ...   
1826    0     0    0     0    0    0    0         0    0    0  ...      0   
1827    0     0    0     0    0    0    0         0    0    0  ...      0   
1828    0     0    0     0    0    0    0         0    0    0  ...      0   
1829    0     0    0     0    0    0    0         0    0    0  ...      0   
1830    0     0    0     0    0    0    0         0    0    0  ...      0   

      zscaler  zte  zuckerberg  zuckerbergs  zuckerman  zurich  zylorion  \

In [14]:
nltk_preprocessed_articles_stem = [','.join(article).replace(',', ' ') for article in nltk_stemmed_articles]
nltk_preprocessed_articles_stem

['with market capit trillion appl nasdaq aapl one world largest compani sinc buffett lieuten initi bought berkshir first million share buffett come appreci appl busi',
 'yahoo financ live anchor discuss inflat fear rise interest rate affect tech sector',
 'dow jone industri averag dive point friday fedex share plung profit warn',
 'arm focus semiconductor softwar design own japanes multin conglomer softbank photo neil hallreut british prime minist liz truss chancellor kwasi kwarteng prepar lastditch effort get cambridg chipmak arm hold list london uk tech firm focus semiconductor softwar design own japanes multin conglomer softbank govern set reignit highlevel talk boss softbank offici mourn period queen elizabeth ii end next week offici said lobbi effort led gerri grimston former invest minist alongsid former prime minist bori johnson resign chri philp exdigit minist work alongsid kwarteng chief secretari treasuri read pound fall low dollar recess loom softbank previous indic want lis

In [15]:
Count_data = CountVec.fit_transform(nltk_preprocessed_articles_stem)
 
nltk_stem_cv_dataframe = pd.DataFrame(Count_data.toarray(),columns=CountVec.get_feature_names())
print(nltk_stem_cv_dataframe)

      aa  aapl  aaplauthor  aaplpricetarget  aarp  ab  abandon  abat  abbey  \
0      0     1           0                0     0   0        0     0      0   
1      0     0           0                0     0   0        0     0      0   
2      0     0           0                0     0   0        0     0      0   
3      0     1           0                0     0   0        0     0      0   
4      0     0           0                0     0   0        0     0      0   
...   ..   ...         ...              ...   ...  ..      ...   ...    ...   
1826   0     0           0                0     0   0        0     0      0   
1827   0     0           0                0     0   0        0     0      0   
1828   0     0           0                0     0   0        0     0      0   
1829   0     0           0                0     0   0        0     0      0   
1830   0     0           0                0     0   0        0     0      0   

      abbi  ...  zoom  zoomin  zscaler  zte  zucker

In [16]:
nltk_stem_frequent_words = list(nltk_stem_cv_dataframe.sum()[nltk_stem_cv_dataframe.sum() > 5].index)

nltk_stem_cv_dataframe[nltk_stem_frequent_words]

aapl  ab  abandon  abat  abbott  abil  abl  abound  abov  aboveaverag  \
0        1   0        0     0       0     0    0       0     0            0   
1        0   0        0     0       0     0    0       0     0            0   
2        0   0        0     0       0     0    0       0     0            0   
3        1   0        0     0       0     0    0       0     0            0   
4        0   0        0     0       0     0    0       0     0            0   
...    ...  ..      ...   ...     ...   ...  ...     ...   ...          ...   
1826     0   0        0     0       0     0    0       0     0            0   
1827     0   0        0     0       0     0    0       0     0            0   
1828     0   0        0     0       0     0    0       0     0            0   
1829     0   0        0     0       0     0    0       0     0            0   
1830     0   0        0     0       0     0    0       0     0            0   

      ...  zhang  zinc  ziprecruit  zm  zone  zoom  zscaler  zte  zuckerberg  \
0     ...      0     0           0   0     0     0        0    0           0   
1     ...      0     0           0   0     0     0        0    0           0   
2     ...      0     0           0   0     0     0        0    0           0   
3     ...      0     0           0   0     0     0        0    0           0   
4     ...      0     0           0   0     0     0        0    0           0   
...   ...    ...   ...         ...  ..   ...   ...      ...  ...         ...   
1826  ...      0     0           0   0     0     0        0    0           0   
1827  ...      0     0           0   0     0     0        0    0           0   
1828  ...      0     0           0   0     1     0        0    0           0   
1829  ...      0     0           0   0     0     0        0    0           0   
1830  ...      0     0           0   0     0     0        0    0           0   

      zylorion  
0            0  
1            0  
2            0  
3            0  
4            0  
...        ...  
1826         0  
1827         0  
1828         0  
1829         0  
1830         0  

[1831 rows x 6115 columns]

In [17]:
nltk_preprocessed_articles_lem = [','.join(article).replace(',', ' ') for article in nltk_lemmatised_articles]
nltk_preprocessed_articles_lem

['With market capitalization trillion Apple NASDAQ AAPL one world largest company Since Buffett lieutenant initially bought Berkshire first million share Buffett come appreciate Apple business',
 'Yahoo Finance Live anchor discus inflation fear rising interest rate affecting tech sector',
 'Dow Jones Industrial Average dived point Friday FedEx share plunged profit warning',
 'Arm focus semiconductor software design owned Japanese multinational conglomerate SoftBank Photo Neil HallReuters British prime minister Liz Truss chancellor Kwasi Kwarteng preparing lastditch effort get Cambridge chipmaker Arm Holdings list London UK tech firm focus semiconductor software design owned Japanese multinational conglomerate SoftBank government set reignite highlevel talk boss SoftBank official mourning period Queen Elizabeth II end next week official said lobbying effort led Gerry Grimstone former investment minister alongside former prime minister Boris Johnson resigned Chris Philp exdigital ministe

In [18]:
Count_data = CountVec.fit_transform(nltk_preprocessed_articles_lem)

nltk_lem_cv_dataframe = pd.DataFrame(Count_data.toarray(),columns=CountVec.get_feature_names())
print(nltk_lem_cv_dataframe)

      aa  aapl  aaplauthorized  aaplpricetargets  aapls  aarp  ab  abandon  \
0      0     1               0                 0      0     0   0        0   
1      0     0               0                 0      0     0   0        0   
2      0     0               0                 0      0     0   0        0   
3      0     1               0                 0      0     0   0        0   
4      0     0               0                 0      0     0   0        0   
...   ..   ...             ...               ...    ...   ...  ..      ...   
1826   0     0               0                 0      0     0   0        0   
1827   0     0               0                 0      0     0   0        0   
1828   0     0               0                 0      0     0   0        0   
1829   0     0               0                 0      0     0   0        0   
1830   0     0               0                 0      0     0   0        0   

      abandoned  abandons  ...  zooms  zscaler  zte  zuckerberg

In [19]:
nltk_lem_frequent_words = list(nltk_lem_cv_dataframe.sum()[nltk_lem_cv_dataframe.sum() > 5].index)

nltk_lem_cv_dataframe[nltk_lem_frequent_words]

aapl  aapls  ab  abandon  abandoned  abbott  ability  able  abound  \
0        1      0   0        0          0       0        0     0       0   
1        0      0   0        0          0       0        0     0       0   
2        0      0   0        0          0       0        0     0       0   
3        1      0   0        0          0       0        0     0       0   
4        0      0   0        0          0       0        0     0       0   
...    ...    ...  ..      ...        ...     ...      ...   ...     ...   
1826     0      0   0        0          0       0        0     0       0   
1827     0      0   0        0          0       0        0     0       0   
1828     0      0   0        0          0       0        0     0       0   
1829     0      0   0        0          0       0        0     0       0   
1830     0      0   0        0          0       0        0     0       0   

      aboveaverage  ...  ziprecruiter  zm  zms  zone  zoom  zscaler  zte  \
0                0  ...             0   0    0     0     0        0    0   
1                0  ...             0   0    0     0     0        0    0   
2                0  ...             0   0    0     0     0        0    0   
3                0  ...             0   0    0     0     0        0    0   
4                0  ...             0   0    0     0     0        0    0   
...            ...  ...           ...  ..  ...   ...   ...      ...  ...   
1826             0  ...             0   0    0     0     0        0    0   
1827             0  ...             0   0    0     0     0        0    0   
1828             0  ...             0   0    0     1     0        0    0   
1829             0  ...             0   0    0     0     0        0    0   
1830             0  ...             0   0    0     0     0        0    0   

      zuckerberg  zuckerbergs  zylorion  
0              0            0         0  
1              0            0         0  
2              0            0         0  
3              0            0         0  
4              0            0         0  
...          ...          ...       ...  
1826           0            0         0  
1827           0            0         0  
1828           0            0         0  
1829           0            0         0  
1830           0            0         0  

[1831 rows x 7843 columns]

In [20]:
spacy_preprocessed_articles_lem = [','.join(article).replace(',', ' ') for article in spacy_lemmatised_articles]
spacy_preprocessed_articles_lem

['With market capitalization trillion Apple NASDAQ AAPL one world largest companies Since Buffett lieutenants initially bought Berkshire first million shares Buffett come appreciate Apple business',
 'Yahoo Finance Live anchors discuss inflation fears rising interest rates affecting tech sector',
 'Dow Jones Industrial Average dived points Friday FedEx shares plunged profit warning',
 'Arm focuses semiconductor software design owned Japanese multinational conglomerate SoftBank Photo Neil HallReuters British prime minister Liz Truss chancellor Kwasi Kwarteng preparing lastditch effort get Cambridge chipmaker Arm Holdings list London UK tech firm focuses semiconductor software design owned Japanese multinational conglomerate SoftBank government set reignite highlevel talks bosses SoftBank official mourning period Queen Elizabeth II ends next week officials said lobbying effort led Gerry Grimstone former investment minister alongside former prime minister Boris Johnson resigned Chris Phil

In [21]:
Count_data = CountVec.fit_transform(spacy_preprocessed_articles_lem)
 
spacy_lem_cv_dataframe = pd.DataFrame(Count_data.toarray(),columns=CountVec.get_feature_names())
print(spacy_lem_cv_dataframe)

      aa  aapl  aaplauthorized  aaplpricetargets  aapls  aarp  ab  abandon  \
0      0     1               0                 0      0     0   0        0   
1      0     0               0                 0      0     0   0        0   
2      0     0               0                 0      0     0   0        0   
3      0     1               0                 0      0     0   0        0   
4      0     0               0                 0      0     0   0        0   
...   ..   ...             ...               ...    ...   ...  ..      ...   
1826   0     0               0                 0      0     0   0        0   
1827   0     0               0                 0      0     0   0        0   
1828   0     0               0                 0      0     0   0        0   
1829   0     0               0                 0      0     0   0        0   
1830   0     0               0                 0      0     0   0        0   

      abandoned  abandons  ...  zooms  zscaler  zte  zuckerberg

In [22]:
spacy_lem_frequent_words = list(spacy_lem_cv_dataframe.sum()[spacy_lem_cv_dataframe.sum() > 5].index)

spacy_lem_cv_dataframe[spacy_lem_frequent_words]

aapl  aapls  ab  abandon  abandoned  abandons  abbott  abilities  \
0        1      0   0        0          0         0       0          0   
1        0      0   0        0          0         0       0          0   
2        0      0   0        0          0         0       0          0   
3        1      0   0        0          0         0       0          0   
4        0      0   0        0          0         0       0          0   
...    ...    ...  ..      ...        ...       ...     ...        ...   
1826     0      0   0        0          0         0       0          0   
1827     0      0   0        0          0         0       0          0   
1828     0      0   0        0          0         0       0          0   
1829     0      0   0        0          0         0       0          0   
1830     0      0   0        0          0         0       0          0   

      ability  able  ...  zms  zone  zones  zoom  zooms  zscaler  zte  \
0           0     0  ...    0     0      0     0      0        0    0   
1           0     0  ...    0     0      0     0      0        0    0   
2           0     0  ...    0     0      0     0      0        0    0   
3           0     0  ...    0     0      0     0      0        0    0   
4           0     0  ...    0     0      0     0      0        0    0   
...       ...   ...  ...  ...   ...    ...   ...    ...      ...  ...   
1826        0     0  ...    0     0      0     0      0        0    0   
1827        0     0  ...    0     0      0     0      0        0    0   
1828        0     0  ...    0     1      0     0      0        0    0   
1829        0     0  ...    0     0      0     0      0        0    0   
1830        0     0  ...    0     0      0     0      0        0    0   

      zuckerberg  zuckerbergs  zylorion  
0              0            0         0  
1              0            0         0  
2              0            0         0  
3              0            0         0  
4              0            0         0  
...          ...          ...       ...  
1826           0            0         0  
1827           0            0         0  
1828           0            0         0  
1829           0            0         0  
1830           0            0         0  

[1831 rows x 8331 columns]

In [23]:
print("Without Smoothing:")
tf_idf_vec = TfidfVectorizer(use_idf=True, 
                        smooth_idf=False,  
                        ngram_range=(1,1),stop_words='english')

tf_idf_data = tf_idf_vec.fit_transform(nltk_preprocessed_articles_stem)
 
nltk_stem_tf_idf_dataframe = pd.DataFrame(tf_idf_data.toarray(),columns = tf_idf_vec.get_feature_names())
print(nltk_stem_tf_idf_dataframe)
print("\n")
  
tf_idf_vec_smooth = TfidfVectorizer(use_idf=True,  
                        smooth_idf=True,  
                        ngram_range=(1,1),stop_words='english')
 
tf_idf_data_smooth = tf_idf_vec_smooth.fit_transform(nltk_preprocessed_articles_stem)
 
print("With Smoothing:")
nltk_stem_tf_idf_dataframe_smooth = pd.DataFrame(tf_idf_data_smooth.toarray(),columns = tf_idf_vec_smooth.get_feature_names())
print(nltk_stem_tf_idf_dataframe_smooth)

Without Smoothing:
       aa      aapl  aaplauthor  aaplpricetarget  aarp   ab  abandon  abat  \
0     0.0  0.171368         0.0              0.0   0.0  0.0      0.0   0.0   
1     0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   
2     0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   
3     0.0  0.022767         0.0              0.0   0.0  0.0      0.0   0.0   
4     0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   
...   ...       ...         ...              ...   ...  ...      ...   ...   
1826  0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   
1827  0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   
1828  0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   
1829  0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   
1830  0.0  0.000000         0.0              0.0   0.0  0.0      0.0   0.0   

      abbey  abbi  ...  zoom  zoomin  zscale

In [24]:
print("Without Smoothing:")
tf_idf_vec = TfidfVectorizer(use_idf=True, 
                        smooth_idf=False,  
                        ngram_range=(1,1),stop_words='english') 
tf_idf_data = tf_idf_vec.fit_transform(nltk_preprocessed_articles_lem)
 
nltk_lem_tf_idf_dataframe = pd.DataFrame(tf_idf_data.toarray(),columns=tf_idf_vec.get_feature_names())
print(nltk_lem_tf_idf_dataframe)
print("\n")
 
tf_idf_vec_smooth = TfidfVectorizer(use_idf=True,  
                        smooth_idf=True,  
                        ngram_range=(1,1),stop_words='english')
 
tf_idf_data_smooth = tf_idf_vec_smooth.fit_transform(nltk_preprocessed_articles_lem)
 
print("With Smoothing:")
nltk_lem_tf_idf_dataframe_smooth = pd.DataFrame(tf_idf_data_smooth.toarray(),columns=tf_idf_vec_smooth.get_feature_names())
print(nltk_lem_tf_idf_dataframe_smooth)

Without Smoothing:
       aa      aapl  aaplauthorized  aaplpricetargets  aapls  aarp   ab  \
0     0.0  0.159019             0.0               0.0    0.0   0.0  0.0   
1     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
2     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
3     0.0  0.022120             0.0               0.0    0.0   0.0  0.0   
4     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
...   ...       ...             ...               ...    ...   ...  ...   
1826  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1827  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1828  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1829  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1830  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   

      abandon  abandoned  abandons  ...  zooms  zscaler  zte  zuckerberg  \
0   

In [25]:
print("Without Smoothing:")

tf_idf_vec = TfidfVectorizer(use_idf=True, 
                        smooth_idf=False,  
                        ngram_range=(1,1),stop_words='english')

tf_idf_data = tf_idf_vec.fit_transform(spacy_preprocessed_articles_lem)
 
spacy_lem_tf_idf_dataframe = pd.DataFrame(tf_idf_data.toarray(),columns=tf_idf_vec.get_feature_names())
print(spacy_lem_tf_idf_dataframe)
print("\n")
 
tf_idf_vec_smooth = TfidfVectorizer(use_idf=True,  
                        smooth_idf=True,  
                        ngram_range=(1,1),stop_words='english')
 
tf_idf_data_smooth = tf_idf_vec_smooth.fit_transform(spacy_preprocessed_articles_lem)
 
print("With Smoothing:")
spacy_lem_tf_idf_dataframe_smooth = pd.DataFrame(tf_idf_data_smooth.toarray(),columns=tf_idf_vec_smooth.get_feature_names())
print(spacy_lem_tf_idf_dataframe_smooth)

Without Smoothing:
       aa      aapl  aaplauthorized  aaplpricetargets  aapls  aarp   ab  \
0     0.0  0.156914             0.0               0.0    0.0   0.0  0.0   
1     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
2     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
3     0.0  0.022001             0.0               0.0    0.0   0.0  0.0   
4     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
...   ...       ...             ...               ...    ...   ...  ...   
1826  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1827  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1828  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1829  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1830  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   

      abandon  abandoned  abandons  ...  zooms  zscaler  zte  zuckerberg  \
0   

In [26]:
article_vector_list = [np.mean([nlp(word).vector for word in article]) for article in nltk_preprocessed_articles_stem] 

np.dot(article_vector_list[0], article_vector_list[1]) / (np.linalg.norm(article_vector_list[0]) * np.linalg.norm(article_vector_list[1]))

1.0

NER

In [27]:
doc = nlp(nltk_preprocessed_articles_stem[0])

entities=[(i, i.label_) for i in doc.ents]
entities

[(buffett, 'PERSON')]

In [28]:
id2word_nltk_stem = corpora.Dictionary(nltk_stemmed_articles)

texts_nltk_stem = nltk_stemmed_articles

corpus_nltk_stem = [id2word_nltk_stem.doc2bow(text) for text in texts_nltk_stem]

print(corpus_nltk_stem[:1])

[[(0, 1), (1, 2), (2, 1), (3, 1), (4, 1), (5, 2), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1)]]


In [29]:
id2word_nltk_lem = corpora.Dictionary(nltk_lemmatised_articles)

texts_nltk_lem = nltk_lemmatised_articles

corpus_nltk_lem = [id2word_nltk_lem.doc2bow(text) for text in texts_nltk_lem]

print(corpus_nltk_lem[:1])

[[(0, 1), (1, 2), (2, 1), (3, 2), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1)]]


In [30]:
id2word_spacy_lem = corpora.Dictionary(spacy_lemmatised_articles)

texts_spacy_lem = spacy_lemmatised_articles

corpus_spacy_lem = [id2word_spacy_lem.doc2bow(text) for text in texts_spacy_lem]

print(corpus_spacy_lem[:1])

[[(0, 1), (1, 2), (2, 1), (3, 2), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1)]]


In [31]:
nltk_stem_lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus_nltk_stem,
                                           id2word=id2word_nltk_stem,
                                           num_topics=10,              # Define the number of topics we want
                                           random_state=100,
                                           update_every=1,             # Determines how often the model parameters should be updated
                                           chunksize=10,               # Number of documents to be used in each training chunk
                                           passes=10,                  # Total number of training passes.
                                           alpha='auto',               # Hyperparameter that affects sparsity of the topics
                                           per_word_topics=True)

In [32]:
nltk_lem_lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus_nltk_lem,
                                           id2word=id2word_nltk_lem,
                                           num_topics=10, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=10,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

In [33]:
spacy_lem_lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus_spacy_lem,
                                           id2word=id2word_spacy_lem,
                                           num_topics=10, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=10,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

In [34]:
pprint(nltk_stem_lda_model.print_topics())
nltk_stem_doc_lda = nltk_stem_lda_model[corpus_nltk_stem]

[(0,
  '0.000*"cross" + 0.000*"costsav" + 0.000*"davita" + 0.000*"custodian" + '
  '0.000*"custodi" + 0.000*"dialysi" + 0.000*"bk" + 0.000*"cincinnati" + '
  '0.000*"distinguish" + 0.000*"citigroup"'),
 (1,
  '0.038*"i" + 0.032*"go" + 0.022*"tax" + 0.020*"and" + 0.018*"realli" + '
  '0.017*"that" + 0.017*"but" + 0.017*"look" + 0.016*"larg" + 0.016*"not"'),
 (2,
  '0.030*"ftc" + 0.025*"inflat" + 0.024*"yield" + 0.022*"index" + '
  '0.022*"market" + 0.021*"gain" + 0.021*"close" + 0.020*"ralli" + '
  '0.017*"point" + 0.016*"tech"'),
 (3,
  '0.029*"amazon" + 0.025*"compani" + 0.015*"deal" + 0.015*"said" + '
  '0.012*"market" + 0.012*"platform" + 0.011*"home" + 0.010*"acquisit" + '
  '0.010*"it" + 0.009*"tech"'),
 (4,
  '0.025*"said" + 0.022*"bloomberg" + 0.020*"china" + 0.013*"us" + '
  '0.011*"antitrust" + 0.011*"read" + 0.011*"last" + 0.010*"inc" + '
  '0.010*"most" + 0.010*"would"'),
 (5,
  '0.097*"appl" + 0.047*"iphon" + 0.037*"devic" + 0.036*"product" + '
  '0.032*"new" + 0.029*"case"

In [35]:
pprint(nltk_lem_lda_model.print_topics())
nltk_lem_doc_lda = nltk_lem_lda_model[corpus_nltk_lem]

[(0,
  '0.033*"stock" + 0.017*"Corporation" + 0.012*"company" + 0.012*"revenue" + '
  '0.011*"growth" + 0.010*"billion" + 0.009*"Apple" + 0.009*"estimate" + '
  '0.008*"year" + 0.008*"share"'),
 (1,
  '0.039*"Amazon" + 0.019*"smart" + 0.017*"Apple" + 0.014*"Disney" + '
  '0.013*"platform" + 0.012*"Finance" + 0.012*"Google" + 0.012*"Yahoo" + '
  '0.011*"streaming" + 0.010*"home"'),
 (2,
  '0.000*"NonHandsets" + 0.000*"Launches" + 0.000*"Upside" + 0.000*"Takeaways" '
  '+ 0.000*"Settlement" + 0.000*"ReadKey" + 0.000*"Probe" + '
  '0.000*"Opportunities" + 0.000*"invalidated" + 0.000*"Luxembourgbased"'),
 (3,
  '0.000*"NonHandsets" + 0.000*"Launches" + 0.000*"Upside" + 0.000*"Takeaways" '
  '+ 0.000*"Settlement" + 0.000*"ReadKey" + 0.000*"Probe" + '
  '0.000*"Opportunities" + 0.000*"invalidated" + 0.000*"Luxembourgbased"'),
 (4,
  '0.031*"Inc" + 0.026*"company" + 0.015*"fund" + 0.015*"million" + '
  '0.014*"stock" + 0.013*"share" + 0.013*"billion" + 0.013*"quarter" + '
  '0.010*"firm" + 0.

In [36]:
pprint(spacy_lem_lda_model.print_topics())
spacy_lem_doc_lda = spacy_lem_lda_model[corpus_spacy_lem]

[(0,
  '0.029*"Bloomberg" + 0.019*"Apple" + 0.019*"said" + 0.016*"Read" + '
  '0.013*"Most" + 0.012*"new" + 0.012*"iPhone" + 0.010*"Roomba" + 0.007*"LP" + '
  '0.007*"Be"'),
 (1,
  '0.023*"Amazon" + 0.021*"Apple" + 0.014*"I" + 0.012*"smart" + 0.010*"not" + '
  '0.009*"Disney" + 0.009*"Finance" + 0.009*"Yahoo" + 0.008*"going" + '
  '0.008*"streaming"'),
 (2,
  '0.000*"Opportunities" + 0.000*"NonHandsets" + 0.000*"invalidated" + '
  '0.000*"handed" + 0.000*"Upside" + 0.000*"Takeaways" + 0.000*"Settlement" + '
  '0.000*"ReadKey" + 0.000*"Probe" + 0.000*"irregularities"'),
 (3,
  '0.283*"earnings" + 0.057*"Street" + 0.054*"case" + 0.054*"Wall" + '
  '0.014*"longer" + 0.013*"bull" + 0.010*"bearish" + 0.007*"turning" + '
  '0.005*"scenario" + 0.005*"lift"'),
 (4,
  '0.014*"said" + 0.013*"company" + 0.012*"companies" + 0.009*"China" + '
  '0.009*"would" + 0.009*"Inc" + 0.008*"market" + 0.007*"year" + '
  '0.007*"Amazons" + 0.006*"Taiwan"'),
 (5,
  '0.023*"FTC" + 0.015*"market" + 0.015*"inflat

In [37]:
print('\nPerplexity: ', nltk_stem_lda_model.log_perplexity(corpus_nltk_stem))  # a measure of how good the model is, the lower the better.

# Compute Coherence Score
nltk_stem_coherence_model_lda = CoherenceModel(model=nltk_stem_lda_model, texts=nltk_stemmed_articles, dictionary=id2word_nltk_stem, coherence='c_v')
coherence_lda = nltk_stem_coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -8.177773599478279

Coherence Score:  0.4426397464456479


In [38]:
# Compute Perplexity
print('\nPerplexity: ', nltk_lem_lda_model.log_perplexity(corpus_nltk_lem))  # a measure of how good the model is, the lower the better.

# Compute Coherence Score
nltk_lem_coherence_model_lda = CoherenceModel(model=nltk_lem_lda_model, texts=nltk_lemmatised_articles, dictionary=id2word_nltk_lem, coherence='c_v')
coherence_lda = nltk_lem_coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -9.087415950175314

Coherence Score:  0.41942231827621823


In [39]:
# Compute Perplexity
print('\nPerplexity: ', spacy_lem_lda_model.log_perplexity(corpus_spacy_lem))  # a measure of how good the model is, the lower the better.

# Compute Coherence Score
spacy_lem_coherence_model_lda = CoherenceModel(model=spacy_lem_lda_model, texts=spacy_lemmatised_articles, dictionary=id2word_spacy_lem, coherence='c_v')
coherence_lda = spacy_lem_coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -9.342378439972707

Coherence Score:  0.44498527275651273


In [40]:
# Visualise the 10 topics 
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(nltk_stem_lda_model, corpus_nltk_stem, id2word_nltk_stem)
vis

/usr/local/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/local/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/local/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/local/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/local/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; se

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
8      0.250970  0.168375       1        1  25.132189
9      0.240046  0.059279       2        1  23.323338
3      0.180111 -0.012858       3        1  15.435556
7      0.021345 -0.244756       4        1  11.144986
4      0.023107 -0.093232       5        1  10.447856
1     -0.045112 -0.252523       6        1   5.716445
5     -0.127261 -0.065326       7        1   4.437447
2     -0.053557  0.216872       8        1   4.360675
6     -0.244824  0.112086       9        1   0.000756
0     -0.244824  0.112086      10        1   0.000753, topic_info=          Term         Freq        Total Category  logprob  loglift
1         appl  4823.000000  4823.000000  Default  30.0000  30.0000
245      stock  7654.000000  7654.000000  Default  29.0000  29.0000
1586      fund  3722.000000  3722.000000  Default  28.0000  28.0000
295     amazon  2668.000000  2668.000000  Default  27.0000  27.0000
668        inc  5140.000000  5140.000000  Default  26.0000  26.0000
...        ...          ...          ...      ...      ...      ...
25     discuss     0.000315   411.647359  Topic10  -9.4402  -2.2870
26        fear     0.000315   365.401724  Topic10  -9.4402  -2.1678
27      financ     0.000315   967.389054  Topic10  -9.4402  -3.1414
28      inflat     0.000315   769.472873  Topic10  -9.4402  -2.9125
29    interest     0.000315   557.523772  Topic10  -9.4402  -2.5903

[559 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
47        2  0.433594      a
47        5  0.445005      a
47        6  0.121235      a
0         2  0.770387   aapl
0         4  0.135666   aapl
...     ...       ...    ...
273       5  0.112763   year
273       7  0.075569   year
1513      8  0.997952  yield
1050      4  0.998762   your
1175      2  0.998473   zack

[668 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[9, 10, 4, 8, 5, 2, 6, 3, 7, 1])

In [41]:
# Visualise the 10 topics 
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(nltk_lem_lda_model, corpus_nltk_lem, id2word_nltk_lem)
vis

/usr/local/lib/python3.9/site-packages/joblib/backports.py:36: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(np.__version__) < '1.13':
/usr/local/lib/python3.9/site-packages/setuptools/_distutils/version.py:346: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  other = LooseVersion(other)
/usr/local/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/local/lib/python3.9/site-packages/joblib/backports.py:36: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(np.__version__) < '1.13':
/usr/local/lib/python3.9/site-packages/joblib/backports.py:36: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(np.__versio

TypeError: Object of type complex is not JSON serializable

PreparedData(topic_coordinates=                        x                   y  topics  cluster       Freq
topic                                                                    
4     -0.187601+0.000000j -0.252200+0.000000j       1        1  30.297867
0     -0.198026+0.000000j -0.208535+0.000000j       2        1  18.957429
9     -0.215353+0.000000j  0.082849+0.000000j       3        1  18.153579
1     -0.136047+0.000000j  0.184896+0.000000j       4        1  10.186004
6     -0.008420+0.000000j  0.095777+0.000000j       5        1   9.927368
5     -0.114997+0.000000j  0.226603+0.000000j       6        1   9.447572
8      0.144275+0.000000j -0.128552+0.000000j       7        1   3.027869
7      0.238723+0.000000j -0.000279+0.000000j       8        1   0.000771
2      0.238723+0.000000j -0.000279+0.000000j       9        1   0.000770
3      0.238723+0.000000j -0.000279+0.000000j      10        1   0.000770, topic_info=          Term         Freq        Total Category  logprob  loglift
2

In [42]:
# Visualise the 10 topics 
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(spacy_lem_lda_model, corpus_spacy_lem, id2word_spacy_lem)
vis

/usr/local/lib/python3.9/site-packages/joblib/backports.py:36: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(np.__version__) < '1.13':
/usr/local/lib/python3.9/site-packages/joblib/backports.py:36: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(np.__version__) < '1.13':
/usr/local/lib/python3.9/site-packages/setuptools/_distutils/version.py:346: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  other = LooseVersion(other)
/usr/local/lib/python3.9/site-packages/setuptools/_distutils/version.py:346: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  other = LooseVersion(other)
/usr/local/lib/python3.9/site-packages/joblib/backports.py:36: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(np.__version__) < '1.13':


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
4     -0.233965  0.013561       1        1  24.961543
9     -0.237953 -0.069824       2        1  20.726305
7     -0.192883 -0.276736       3        1  20.354461
1     -0.138336  0.241138       4        1  17.106602
0     -0.048577  0.280896       5        1  10.281907
5     -0.057710 -0.082668       6        1   6.040856
3      0.254819 -0.037638       7        1   0.526017
8      0.218201 -0.022910       8        1   0.000769
2      0.218201 -0.022910       9        1   0.000769
6      0.218201 -0.022910      10        1   0.000769, topic_info=          Term         Freq        Total Category  logprob  loglift
708        Inc  5114.000000  5114.000000  Default  30.0000  30.0000
305   earnings   783.000000   783.000000  Default  29.0000  29.0000
678  Bloomberg  1583.000000  1583.000000  Default  28.0000  28.0000
1        Apple  3880.000000  3880.000000  Default  27.0000  27.0000
315     Amazon  2369.000000  2369.000000  Default  26.0000  26.0000
..         ...          ...          ...      ...      ...      ...
25       Yahoo     0.000191   768.194390  Topic10  -9.9621  -3.4328
26   affecting     0.000191     0.675620  Topic10  -9.9621   3.6033
27     anchors     0.000191    25.298125  Topic10  -9.9621  -0.0195
28     discuss     0.000191   228.323407  Topic10  -9.9621  -2.2196
29       fears     0.000191   102.629687  Topic10  -9.9621  -1.4199

[533 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
0         1  0.068102       AAPL
0         2  0.785601       AAPL
0         4  0.145932       AAPL
1295      1  0.129698  According
1295      2  0.868410  According
...     ...       ...        ...
294       4  0.087218      would
296       1  0.381519       year
296       2  0.477427       year
296       5  0.140693       year
2469      6  0.998014      yield

[455 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[5, 10, 8, 2, 1, 6, 4, 9, 3, 7])

In [44]:
print(type(spacy_lem_tf_idf_dataframe_smooth)) #this is fdf
print(type(spacy_lem_lda_model))
print(type(corpus_spacy_lem))
print(type(id2word_spacy_lem))

<class 'pandas.core.frame.DataFrame'>
<class 'gensim.models.ldamodel.LdaModel'>
<class 'list'>
<class 'gensim.corpora.dictionary.Dictionary'>


In [46]:
fdf = spacy_lem_tf_idf_dataframe_smooth

In [47]:
df

date  \
0     2022-09-16T14:00:00+00:00   
1     2022-09-16T13:49:38+00:00   
2     2022-09-16T13:35:41+00:00   
3     2022-09-16T13:34:07+00:00   
4     2022-09-16T12:53:41+00:00   
...                         ...   
1826  2022-08-05T21:20:00+00:00   
1827  2022-08-05T21:18:07+00:00   
1828  2022-08-05T21:02:17+00:00   
1829  2022-08-05T20:45:00+00:00   
1830  2022-08-05T20:22:45+00:00   

                                                  title  \
0                        Why Warren Buffett Loves Apple   
1     Big Tech stocks face difficulty beyond rising ...   
2     Dow Jones Sells Off As FedEx Plunges 23% On Pr...   
3     ARM listing: Why UK is desperate for Cambridge...   
4     Dow Jones Futures Sell Off As FedEx Plunges 20...   
...                                                 ...   
1826  Advertising Is Still Going Strong. Apple Wants...   
1827  Dow Jones Futures: Market Rally Resilient; App...   
1828  President Xi may use Speaker Pelosi's visit to...   
1829           The Best Multiport Wall Adapters of 2022   
1830  Amazon’s iRobot Deal Seen Facing Tough FTC Ant...   

                                                content    neg    pos  \
0     With a market capitalization of 25 trillion Ap...  0.000  0.129   
1     Yahoo Finance Live anchors discuss how inflati...  0.128  0.138   
2     The Dow Jones Industrial Average dived 350 poi...  0.102  0.217   
3     Arm which focuses on semiconductor and softwar...  0.040  0.048   
4     Dow Jones futures dropped 350 points Friday mo...  0.107  0.227   
...                                                 ...    ...    ...   
1826  A recent job listing suggests Apple is interes...  0.000  0.204   
1827  The market rally showed resilience after Frida...  0.000  0.000   
1828  Susan Shirk UC San Diego Research Professor an...  0.038  0.096   
1829  If you're tired of having all your gadgets spr...  0.165  0.094   
1830  Bloomberg  Amazoncom Inc is barrelling ahead w...  0.066  0.134   

      movement  subjectivity     polar  
0            0      0.166667  0.125000  
1            0      0.500000  0.136364  
2            0      0.450000  0.175000  
3            0      0.345402  0.086509  
4            0      0.500000  0.500000  
...        ...           ...       ...  
1826         1      0.283333  0.183333  
1827         1      0.000000  0.000000  
1828         1      0.401906  0.108931  
1829         1      0.400000 -0.216667  
1830         1      0.448494  0.099294  

[1831 rows x 8 columns]

In [48]:
fdf

aa      aapl  aaplauthorized  aaplpricetargets  aapls  aarp   ab  \
0     0.0  0.157635             0.0               0.0    0.0   0.0  0.0   
1     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
2     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
3     0.0  0.022271             0.0               0.0    0.0   0.0  0.0   
4     0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
...   ...       ...             ...               ...    ...   ...  ...   
1826  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1827  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1828  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1829  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   
1830  0.0  0.000000             0.0               0.0    0.0   0.0  0.0   

      abandon  abandoned  abandons  ...  zooms  zscaler  zte  zuckerberg  \
0         0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
1         0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
2         0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
3         0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
4         0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
...       ...        ...       ...  ...    ...      ...  ...         ...   
1826      0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
1827      0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
1828      0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
1829      0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   
1830      0.0        0.0       0.0  ...    0.0      0.0  0.0         0.0   

      zuckerbergs  zuckerman  zurich  zylorion  zynga  âœthe  
0             0.0        0.0     0.0       0.0    0.0    0.0  
1             0.0        0.0     0.0       0.0    0.0    0.0  
2             0.0        0.0     0.0       0.0    0.0    0.0  
3             0.0        0.0     0.0       0.0    0.0    0.0  
4             0.0        0.0     0.0       0.0    0.0    0.0  
...           ...        ...     ...       ...    ...    ...  
1826          0.0        0.0     0.0       0.0    0.0    0.0  
1827          0.0        0.0     0.0       0.0    0.0    0.0  
1828          0.0        0.0     0.0       0.0    0.0    0.0  
1829          0.0        0.0     0.0       0.0    0.0    0.0  
1830          0.0        0.0     0.0       0.0    0.0    0.0  

[1831 rows x 17791 columns]

In [52]:
y = df['movement']

In [55]:
import scipy

In [56]:
x = scipy.sparse.csr_matrix(fdf.values)

In [58]:
type(x)

scipy.sparse.csr.csr_matrix

In [59]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=69)


In [60]:
type(x_train)

scipy.sparse.csr.csr_matrix

In [62]:
x_train = x_train.toarray()
type(x_train)

numpy.ndarray

In [64]:
fdf.to_csv("sparse_matrix.csv");

In [63]:
import tensorflow as tf

In [65]:
ann = tf.keras.models.Sequential()
ann.add(tf.keras.layers.Dense(units=6, activation='relu'))
ann.add(tf.keras.layers.Dense(units=6, activation='relu'))
ann.add(tf.keras.layers.Dense(units=6, activation='softmax'))
ann.add(tf.keras.layers.Dense(units=1, activation='sigmoid'))
ann.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

2022-10-17 21:18:19.099733: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [66]:
ann.fit(x_train, y_train, batch_size=32, epochs=500, verbose=1)

Epoch 1/500
41/41 [==============================] - 1s 2ms/step - loss: 0.6841 - accuracy: 0.5667
Epoch 2/500
41/41 [==============================] - 0s 2ms/step - loss: 0.6801 - accuracy: 0.5667
Epoch 3/500
41/41 [==============================] - 0s 2ms/step - loss: 0.6656 - accuracy: 0.5667
Epoch 4/500
41/41 [==============================] - 0s 2ms/step - loss: 0.6308 - accuracy: 0.6237
Epoch 5/500
41/41 [==============================] - 0s 2ms/step - loss: 0.5668 - accuracy: 0.8860
Epoch 6/500
41/41 [==============================] - 0s 2ms/step - loss: 0.4909 - accuracy: 0.9680
Epoch 7/500
41/41 [==============================] - 0s 2ms/step - loss: 0.4266 - accuracy: 0.9813
Epoch 8/500
41/41 [==============================] - 0s 2ms/step - loss: 0.3794 - accuracy: 0.9859
Epoch 9/500
41/41 [==============================] - 0s 2ms/step - loss: 0.3459 - accuracy: 0.9867
Epoch 10/500
41/41 [==============================] - 0s 2ms/step - loss: 0.3201 - accuracy: 0.9930
Epoch 11/

41/41 [==============================] - 0s 2ms/step - loss: 0.0493 - accuracy: 0.9953
Epoch 84/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0479 - accuracy: 0.9969
Epoch 85/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0471 - accuracy: 0.9969
Epoch 86/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0465 - accuracy: 0.9953
Epoch 87/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0462 - accuracy: 0.9969
Epoch 88/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0451 - accuracy: 0.9961
Epoch 89/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0445 - accuracy: 0.9969
Epoch 90/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0438 - accuracy: 0.9961
Epoch 91/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0425 - accuracy: 0.9969
Epoch 92/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0420 - accuracy: 0.9969
Epoch 93/500


41/41 [==============================] - 0s 2ms/step - loss: 0.0101 - accuracy: 0.9969
Epoch 246/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0100 - accuracy: 0.9969
Epoch 247/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0100 - accuracy: 0.9969
Epoch 248/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0100 - accuracy: 0.9969
Epoch 249/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0098 - accuracy: 0.9969
Epoch 250/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0100 - accuracy: 0.9969
Epoch 251/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0098 - accuracy: 0.9969
Epoch 252/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0101 - accuracy: 0.9969
Epoch 253/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0099 - accuracy: 0.9969
Epoch 254/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0096 - accuracy: 0.9969
Epoc

41/41 [==============================] - 0s 1ms/step - loss: 0.0072 - accuracy: 0.9969
Epoch 408/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0073 - accuracy: 0.9969
Epoch 409/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0072 - accuracy: 0.9969
Epoch 410/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0071 - accuracy: 0.9969
Epoch 411/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0072 - accuracy: 0.9969
Epoch 412/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0072 - accuracy: 0.9969
Epoch 413/500
41/41 [==============================] - 0s 1ms/step - loss: 0.0071 - accuracy: 0.9969
Epoch 414/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0071 - accuracy: 0.9969
Epoch 415/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0071 - accuracy: 0.9969
Epoch 416/500
41/41 [==============================] - 0s 2ms/step - loss: 0.0071 - accuracy: 0.9969
Epoc

In [67]:
def matrix_to_tensor(x):
    coo = x.tocoo()
    indices = np.mat([coo.row, coo.col]).transpose()
    return tf.SparseTensor(indices, coo.data, coo.shape)

In [68]:
x_test = matrix_to_tensor(x_test)

In [104]:
y_pred = ann.predict(tf.sparse.reorder(x_test))
y_pred

array([[9.99856532e-01],
       [9.99862611e-01],
       [1.21999961e-04],
       [9.99858737e-01],
       [9.99863148e-01],
       [1.20373188e-04],
       [1.21483426e-04],
       [1.21663827e-04],
       [9.93765414e-01],
       [1.20871744e-04],
       [1.22102269e-04],
       [1.20972647e-04],
       [7.16976941e-01],
       [1.20816774e-04],
       [9.99862850e-01],
       [1.21298886e-04],
       [7.53541052e-01],
       [9.99860287e-01],
       [9.99856591e-01],
       [9.99861121e-01],
       [9.99860883e-01],
       [9.99544621e-01],
       [9.71900821e-02],
       [9.99856949e-01],
       [2.18202114e-01],
       [8.37506533e-01],
       [9.99863088e-01],
       [9.99856055e-01],
       [9.98765945e-01],
       [1.20337718e-04],
       [1.20840625e-04],
       [9.99860764e-01],
       [9.99544621e-01],
       [9.99863505e-01],
       [9.99862313e-01],
       [1.23339807e-04],
       [9.99842405e-01],
       [1.20534583e-04],
       [9.99441028e-01],
       [1.20465287e-04],


In [105]:
#for i in range(len(y_pred)):
    #y_pred[i][0] = float(y_pred[i][0])
y_pred = (y_pred > 0.4)

In [107]:
from sklearn.metrics import classification_report, confusion_matrix

In [108]:
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))

[[205  40]
 [ 10 295]]
              precision    recall  f1-score   support

           0       0.95      0.84      0.89       245
           1       0.88      0.97      0.92       305

    accuracy                           0.91       550
   macro avg       0.92      0.90      0.91       550
weighted avg       0.91      0.91      0.91       550



In [109]:
y_pred

array([[ True],
       [ True],
       [False],
       [ True],
       [ True],
       [False],
       [False],
       [False],
       [ True],
       [False],
       [False],
       [False],
       [ True],
       [False],
       [ True],
       [False],
       [ True],
       [ True],
       [ True],
       [ True],
       [ True],
       [ True],
       [False],
       [ True],
       [False],
       [ True],
       [ True],
       [ True],
       [ True],
       [False],
       [False],
       [ True],
       [ True],
       [ True],
       [ True],
       [False],
       [ True],
       [False],
       [ True],
       [False],
       [False],
       [False],
       [ True],
       [ True],
       [False],
       [False],
       [False],
       [ True],
       [ True],
       [False],
       [False],
       [ True],
       [False],
       [ True],
       [ True],
       [ True],
       [ True],
       [ True],
       [ True],
       [ True],
       [ True],
       [ True],
       [

In [111]:
from sklearn.metrics import matthews_corrcoef

In [112]:
matthews = matthews_corrcoef(y_test, y_pred)
print(matthews)

0.8188779634995198
